In [1]:
# 1. Import Plotly
import plotly.graph_objects as go
import pandas as pd
import glob
from pathlib import Path

In [2]:
# find relevant data files
csv_files = glob.glob("../logs/imu_driver_data_*.csv")
print(f"found {len(csv_files)} files: ")
for file in csv_files:
    print(f" - {file}")

# load the most recent file
latest_file = max(csv_files, key=lambda f: Path(f).stat().st_mtime)
df = pd.read_csv(latest_file)
print(f"Loaded {len(df)} data points")

found 2 files: 
 - ../logs/imu_driver_data_20251121_030556.csv
 - ../logs/imu_driver_data_20251121_053025.csv
Loaded 40015 data points


In [3]:
# check data structure
print("data shape:", df.shape);
print("\nColumns:", df.columns.tolist())
print("\nFirst few rows:")
df.head()

data shape: (40015, 12)

Columns: ['timestamp_ns', 'timestamp_sec', 'accel_x_g', 'accel_y_g', 'accel_z_g', 'gyro_x_dps', 'gyro_y_dps', 'gyro_z_dps', 'mag_x_gauss', 'mag_y_gauss', 'mag_z_gauss', 'temperature_c']

First few rows:


timestamp_ns  timestamp_sec  accel_x_g  accel_y_g  accel_z_g  \
0  143722856329096  143722.856329  -0.114680   1.010587  -0.020008   
1  143722865041183  143722.865041  -0.115351   1.035109  -0.020069   
2  143722873971469  143722.873971  -0.108153   0.982344  -0.017507   
3  143722882678116  143722.882678  -0.108153   0.982344  -0.017019   
4  143722891793956  143722.891794  -0.114741   1.015772  -0.017019   

   gyro_x_dps  gyro_y_dps  gyro_z_dps  mag_x_gauss  mag_y_gauss  mag_z_gauss  \
0       0.569      -1.846      -5.626      0.14112     -0.51064      0.06856   
1       0.779      -1.969      -5.530      0.14112     -0.51064      0.06856   
2       0.674      -2.205      -5.451      0.13432     -0.50688      0.07664   
3       0.560      -2.249      -5.898      0.13432     -0.50688      0.07664   
4       0.560      -2.249      -5.338      0.13696     -0.50976      0.06744   

   temperature_c  
0          23.75  
1          23.75  
2          23.88  
3          23.88  
4          24.00

In [4]:
# Create time column
df['time_sec'] = (df['timestamp_ns'] - df['timestamp_ns'].iloc[0]) / 1e9

# Simple 2D line plot
fig = go.Figure()
fig.add_trace(go.Scatter(x=df['time_sec'], y=df['accel_x_g'], name='Accel X'))
fig.add_trace(go.Scatter(x=df['time_sec'], y=df['accel_y_g'], name='Accel Y'))
fig.add_trace(go.Scatter(x=df['time_sec'], y=df['accel_z_g'], name='Accel Z'))
fig.update_layout(title='Accelerometer Data', xaxis_title='Time (s)', yaxis_title='g')
fig.show()

# Simple 2D line plot
fig = go.Figure()
fig.add_trace(go.Scatter(x=df['time_sec'], y=df['gyro_x_dps'], name='Gyro X'))
fig.add_trace(go.Scatter(x=df['time_sec'], y=df['gyro_y_dps'], name='Gyro Y'))
fig.add_trace(go.Scatter(x=df['time_sec'], y=df['gyro_z_dps'], name='Gyro Z'))
fig.update_layout(title='Gyroscope Data', xaxis_title='Time (s)', yaxis_title='Degrees per second')
fig.show()

fig = go.Figure()
fig.add_trace(go.Scatter(x=df['time_sec'], y=df['mag_x_gauss'], name='Mag X'))
fig.add_trace(go.Scatter(x=df['time_sec'], y=df['mag_y_gauss'], name='Mag Y'))
fig.add_trace(go.Scatter(x=df['time_sec'], y=df['mag_z_gauss'], name='Mag Z'))
fig.update_layout(title='Magnetometer Data', xaxis_title='Time (s)', yaxis_title='Gauss')
fig.show()

In [5]:
# import the function from a local module named compute_octant_distro.py
from ellipsoid_fitting_utils import compute_octant_distro
from ellipsoid_fitting_utils import extract_octant_consistent_data
from ellipsoid_fitting_utils import fit_ellipsoid

# compute octant distribution for ellipsoid analysis
compute_octant_distro(df['mag_x_gauss'], df['mag_y_gauss'], df['mag_z_gauss'])
df_balanced = extract_octant_consistent_data(df['mag_x_gauss'], df['mag_y_gauss'], df['mag_z_gauss'])
fit_ellipsoid(df_balanced['x'], df_balanced['y'], df_balanced['z'])




 DATA VARIATION ANALYSIS

1. DATA RANGE CHECK:
   X: [-0.508560, 0.626000]
      Range: 1.134560
      Std:   0.219101
   Y: [-0.908720, 0.432800]
      Range: 1.341520
      Std:   0.362344
   Z: [-0.875680, 0.200240]
      Range: 1.075920
      Std:   0.250855

2. MAGNITUDE ANALYSIS:
   Mean:   0.641578
   Std:    0.211888
   Range:  [0.122390, 1.033565]
   CV:     33.03%

3. SPHERICAL COVERAGE CHECK:
   Octant distribution (should be balanced):
      Octant 0:   513 samples (  1.3%) 
      Octant 1:  2393 samples (  6.0%) ██
      Octant 2:  9677 samples ( 24.2%) ████████████
      Octant 3:  6858 samples ( 17.1%) ████████
      Octant 4:   433 samples (  1.1%) 
      Octant 5:  4161 samples ( 10.4%) █████
      Octant 6:  2700 samples (  6.7%) ███
      Octant 7: 13280 samples ( 33.2%) ████████████████

4. DATA QUALITY ASSESSMENT:
   Range balance ratio: 0.802
   ✓ Data appears well distributed
   ⚠️  WARNING: Poor spherical coverage
      Minimum octant coverage: 1.1% (should be >

In [6]:
compute_octant_distro(df['accel_x_g'], df['accel_y_g'], df['accel_z_g'])
df_balanced = extract_octant_consistent_data(df['accel_x_g'], df['accel_y_g'], df['accel_z_g'])
fit_ellipsoid(df_balanced['x'], df_balanced['y'], df_balanced['z'])

 DATA VARIATION ANALYSIS

1. DATA RANGE CHECK:
   X: [-1.205848, 0.936533]
      Range: 2.142381
      Std:   0.263791
   Y: [-1.078419, 1.400438]
      Range: 2.478857
      Std:   0.694596
   Z: [-1.071160, 1.021323]
      Range: 2.092483
      Std:   0.389576

2. MAGNITUDE ANALYSIS:
   Mean:   1.017927
   Std:    0.038055
   Range:  [0.633558, 1.460494]
   CV:     3.74%

3. SPHERICAL COVERAGE CHECK:
   Octant distribution (should be balanced):
      Octant 0:   890 samples (  2.2%) █
      Octant 1:  1086 samples (  2.7%) █
      Octant 2:  2068 samples (  5.2%) ██
      Octant 3:  2491 samples (  6.2%) ███
      Octant 4:  4393 samples ( 11.0%) █████
      Octant 5: 24678 samples ( 61.7%) ██████████████████████████████
      Octant 6:  1289 samples (  3.2%) █
      Octant 7:  3120 samples (  7.8%) ███

4. DATA QUALITY ASSESSMENT:
   Range balance ratio: 0.844
   ✓ Data appears well distributed
   ⚠️  WARNING: Poor spherical coverage
      Minimum octant coverage: 2.2% (should be >1